<a href="https://colab.research.google.com/github/MohammedZ666/BageNet/blob/main/tflite_converter.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Download dataset

In [2]:
!gdown --fuzzy https://drive.google.com/file/d/1vxFk8ypDTqT1J3PteZIaS2d1ApPvFItz/view?usp=sharing
!unzip Merged_Split.zip
!rm -rf Merged_Split.zip

Streaming output truncated to the last 5000 lines.
  inflating: Merged_Split/train/cardboard/cardboard283.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_1866.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_521.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_60.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_44.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_1210.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_2200.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_100.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_243.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_729.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_1675.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_1014.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_1207.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_1759.jpg  
  inflating: Merged_Split/train/cardboard/cardboard_1168.jpg  
  inflating: M

In [3]:
!pip install ai-edge-model-explorer
!pip install -q tensorflow-model-optimization

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 23.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.7/84.7 MB 9.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 52.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 242.5/242.5 kB 4.2 MB/s eta 0:00:00


# Initialize Dataset

In [1]:
import tensorflow as tf
import os

print("TensorFlow version:", tf.__version__)

from tensorflow.keras.metrics import F1Score


from tensorflow_model_optimization.python.core.keras.compat import keras
from tensorflow_model_optimization.python.core.quantization.keras import quantize

from tensorflow.keras.preprocessing.image import ImageDataGenerator
import tensorflow as tf
import numpy as np

output_dir = '/content/Merged_Split'  # Where to save the split dataset

# Set image dimensions
BATCH_SIZE = 16
IMG_DIM = 51
NUM_CLASSES = 6

# Image augmentation function
def custom_augmentation(image):
    # Resize the image
    image = tf.image.resize(image, (IMG_DIM, IMG_DIM))

    # Random Horizontal Flip with probability 0.3
    image = tf.image.random_flip_left_right(image, seed=1)  # Random flip

    # Random Rotation by 15 degrees
    image = tf.image.rot90(image, k=np.random.randint(4))  # Random rotation by 90, 180, 270, or 360 degrees

    # Color Jitter (Brightness, Contrast, Saturation, Hue)
    image = tf.image.random_brightness(image, max_delta=0.1)
    image = tf.image.random_contrast(image, lower=0.95, upper=1.05)
    image = tf.image.random_saturation(image, lower=0.95, upper=1.05)
    image = tf.image.random_hue(image, max_delta=0.05)

    # Normalize (Mean, Std for normalization) - normalization based on your values
    image = tf.image.per_image_standardization(image)  # Standardization to zero mean and unit variance

    return image

# ImageDataGenerator for data augmentation (optional) and preprocessing
train_datagen = ImageDataGenerator(rescale=1./255)  # Normalize pixel values to [0, 1]
val_datagen = ImageDataGenerator(rescale=1./255)    # Only rescaling for validation data
test_datagen = ImageDataGenerator(rescale=1./255)   # Only rescaling for test data

loss = 'categorical'
# Load data from the split directories
train_dataset = train_datagen.flow_from_directory(
    directory=f'{output_dir}/train',  # Path to train images
    target_size=(IMG_DIM, IMG_DIM),
    batch_size=BATCH_SIZE,
    class_mode=loss  # For multi-class classification with integer labels
)

val_dataset = val_datagen.flow_from_directory(
    directory=f'{output_dir}/val',  # Path to validation images
    target_size=(IMG_DIM, IMG_DIM),
    batch_size=BATCH_SIZE,
    class_mode=loss  # For multi-class classification with integer labels
)

test_dataset = test_datagen.flow_from_directory(
    directory=f'{output_dir}/test',  # Path to test images
    target_size=(IMG_DIM, IMG_DIM),
    batch_size=BATCH_SIZE,
    class_mode=loss  # For multi-class classification with integer labels
)

# Checking the class indices manually
class_indices = train_dataset.class_indices
print("Class indices: ", class_indices)

# Create a generator function for the train dataset
def generator(dataset):
    while True:
        for x_batch, y_batch in dataset:
            yield x_batch, y_batch

# Convert the DirectoryIterator to a tf.data.Dataset
train_dataset_tf = tf.data.Dataset.from_generator(
    lambda: generator(train_dataset),  # Pass the generator function
    output_types=(tf.float32, tf.int32),  # Specify output types
    output_shapes=(
        tf.TensorShape([None, IMG_DIM, IMG_DIM, 3]),  # Image shape
        tf.TensorShape([None, NUM_CLASSES])  # Label shape
    )
)

# Apply the custom augmentation to the training set
train_dataset_tf = train_dataset_tf.map(lambda x, y: (tf.py_function(custom_augmentation, [x], tf.float32), y))

# Optionally apply similar to validation and test datasets (if you need any augmentation for them)
val_dataset_tf = tf.data.Dataset.from_generator(
    lambda: generator(val_dataset),
    output_types=(tf.float32, tf.int32),  # Specify output types
    output_shapes=(
        tf.TensorShape([None, IMG_DIM, IMG_DIM, 3]),  # Image shape
        tf.TensorShape([None, NUM_CLASSES])  # Label shape
    )
)

test_dataset_tf = tf.data.Dataset.from_generator(
    lambda: generator(test_dataset),
    output_types=(tf.float32, tf.int32),  # Specify output types
    output_shapes=(
        tf.TensorShape([None, IMG_DIM, IMG_DIM, 3]),  # Image shape
        tf.TensorShape([None, NUM_CLASSES])  # Label shape
    )
)

TensorFlow version: 2.17.1
Found 14468 images belonging to 6 classes.
Found 1810 images belonging to 6 classes.
Found 1812 images belonging to 6 classes.


Instructions for updating:
Use output_signature instead
Instructions for updating:
Use output_signature instead


Class indices:  {'cardboard': 0, 'glass': 1, 'metal': 2, 'paper': 3, 'plastic': 4, 'trash': 5}


# Declaring Tensorflow Model

In [2]:
layers = [
    # Initial Convolution layer with reduced filters
    quantize.quantize_annotate_layer(keras.layers.Conv2D(16, kernel_size=(3, 3), strides=(2, 2), padding="same", activation='relu', input_shape=(IMG_DIM, IMG_DIM, 3))),
    keras.layers.BatchNormalization(),

    # Depthwise Separable Convolution Block 1 with fewer filters
    keras.layers.DepthwiseConv2D(kernel_size=(3, 3), padding="same", activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.Conv2D(32, kernel_size=(1, 1), activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.AveragePooling2D(pool_size=(2, 2), strides=(2, 2)),

    # Depthwise Separable Convolution Block 2 with fewer filters
    keras.layers.DepthwiseConv2D(kernel_size=(3, 3), padding="same", activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.Conv2D(64, kernel_size=(1, 1), activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.AveragePooling2D(pool_size=(2, 2), strides=(2, 2)),
    keras.layers.Dropout(0.2),  # Dropout after pooling

    # Depthwise Separable Convolution Block 3 with fewer filters
    keras.layers.DepthwiseConv2D(kernel_size=(3, 3), padding="same", activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.Conv2D(128, kernel_size=(1, 1), activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.AveragePooling2D(pool_size=(2, 2), strides=(2, 2)),
    keras.layers.Dropout(0.3),
    # Final Depthwise Separable Convolution Block with reduced filters
    keras.layers.DepthwiseConv2D(kernel_size=(3, 3), padding="same", activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.Conv2D(128, kernel_size=(1, 1), activation='relu'),  # Reduced number of filters
    keras.layers.BatchNormalization(),
    keras.layers.GlobalAveragePooling2D(),  # GlobalAveragePooling reduces parameters

    # Fully connected layers with reduced units
    keras.layers.Dense(64, activation='relu'),  # Reduced dense layer size
    keras.layers.Dropout(0.6),  # Dropout layer after first dense layer
    keras.layers.Dense(32, activation='relu'),  # Reduced dense layer size
    keras.layers.Dropout(0.6),  # Dropout layer after second dense layer

    # Output layer with softmax activation for multi-class classification
    keras.layers.Dense(6, activation='softmax')  # 6 classes with softmax activation
]

keras_file = 'model.h5'


tf_model = keras.Sequential(layers)
# tf_model = quantize.quantize_apply(tf_model)

tf_model.compile(
    loss=keras.losses.categorical_crossentropy,
    optimizer=keras.optimizers.Adam(),
    metrics=['accuracy', F1Score()],)

x = tf.random.uniform(shape=(BATCH_SIZE, IMG_DIM, IMG_DIM, 3), maxval=1, minval=0)
print(tf_model(x).shape)
keras.models.save_model(tf_model, keras_file)
tf_model.summary()

(16, 6)
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 quantize_annotate (Quantiz  (None, 26, 26, 16)        448       
 eAnnotate)                                                      
                                                                 
 batch_normalization (Batch  (None, 26, 26, 16)        64        
 Normalization)                                                  
                                                                 
 depthwise_conv2d (Depthwis  (None, 26, 26, 16)        160       
 eConv2D)                                                        
                                                                 
 batch_normalization_1 (Bat  (None, 26, 26, 16)        64        
 chNormalization)                                                
                                                                 
 conv2d_1 (Conv2D)           (None, 26, 26, 32) 

<ipython-input-2-a6fad04923d6>:58: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native TF-Keras format, e.g. `model.save('my_model.keras')`.
  keras.models.save_model(tf_model, keras_file)


Trainable params: 42086 (164.40 KB)
Non-trainable params: 1216 (4.75 KB)
_________________________________________________________________


# Train Model

In [3]:
from tqdm.keras import TqdmCallback
from tensorflow.keras.metrics import Accuracy, F1Score
import tensorflow as tf
import numpy as np


steps_per_epoch_train = np.ceil(train_dataset.samples / BATCH_SIZE).astype(int)

epochs=1

for i in range(epochs):
  history = tf_model.fit(
      train_dataset_tf,  # Use the tf.data.Dataset here
      steps_per_epoch=steps_per_epoch_train,  # Steps per epoch should be based on tf.data
      epochs=1,
      callbacks=[TqdmCallback()],
  )
  tf_model.evaluate(val_dataset_tf,
                    steps=len(val_dataset))

keras.models.save_model(tf_model, keras_file)
# Evaluate the model on test data
test_loss, test_acc = tf_model.evaluate(test_dataset_tf, steps=len(test_dataset))  # Use tf.data.Dataset for test
print("Test Accuracy: ", test_acc)

0epoch [00:00, ?epoch/s]

0batch [00:00, ?batch/s]

KeyboardInterrupt: 

In [4]:
with quantize.quantize_scope():
  tF_model = keras.models.load_model(keras_file)

score = tf_model.evaluate(test_dataset_tf.take(1), verbose=1, steps=len(test_dataset))

print('Test Loss:', score[0])
print('Test Accuracy:', score[1])
print('Test F1Score:', score[2])

  1/114 [..............................] - ETA: 4:57 - loss: 1.7918 - accuracy: 0.2500 - f1_score: 0.0667

114/114 [==============================] - 3s 1ms/step - loss: 1.7918 - accuracy: 0.2500 - f1_score: 0.0667
Test Loss: 1.7917569875717163
Test Accuracy: 0.25
Test F1Score: 0.06666666269302368


# Convert to TFLite

In [5]:
subset = 1

# Use the first 300 images in the post-training quantization.
def representative_dataset():
  for i in range(subset):
    image, _ = next(iter(train_dataset_tf))
    yield [image]

with quantize.quantize_scope():
  tF_model = keras.models.load_model(keras_file)
converter = tf.lite.TFLiteConverter.from_keras_model(tf_model)
converter.optimizations = [tf.lite.Optimize.DEFAULT]
converter._experimental_disable_per_channel_quantization_for_dense_layers = True
converter.representative_dataset = representative_dataset
converter.target_spec.supported_ops = [tf.lite.OpsSet.TFLITE_BUILTINS_INT8]
converter.inference_input_type = tf.int8
converter.inference_output_type = tf.int8
tflite_model = converter.convert()
quant_file = 'model.tflite'
open(quant_file, 'wb').write(tflite_model)

/usr/local/lib/python3.10/dist-packages/tensorflow/lite/python/convert.py:983: UserWarning: Statistics for quantized inputs were expected, but not specified; continuing anyway.
  warnings.warn(


68840

# Compare File Sizes Between Base and Tflite Model

In [6]:
import os


float_converter = tf.lite.TFLiteConverter.from_keras_model(tf_model)
float_tflite_model = float_converter.convert()


float_file = "float_model.tflite"

with open(float_file, 'wb') as f:
  f.write(float_tflite_model)

print("Float model in Mb:", os.path.getsize(float_file) / float(2**20))
print("Quantized model in Mb:", os.path.getsize(quant_file) / float(2**20))

Float model in Mb: 0.164642333984375
Quantized model in Mb: 0.06565093994140625


# Evalute TFLite Model

In [7]:
# Evaluate the fully quantized model.
interpreter = tf.lite.Interpreter(model_path=quant_file)
interpreter.resize_tensor_input(0, [1, IMG_DIM, IMG_DIM, 3])
interpreter.allocate_tensors()
input_details = interpreter.get_input_details()
output_details = interpreter.get_output_details()
input_index = input_details[0]['index']
output_index = output_details[0]['index']
print(f"Input shape: {input_details[0]['shape_signature']}, Output shape: {output_details[0]['shape_signature']}")


total_seen = 0
num_correct = 0

# Testing the entire dataset is too slow. Verifying only 300 of 10k samples.
print('Evaluate TFLite model.')


for imgs, label in test_dataset_tf.take(subset):
  total_seen += imgs.shape[0]
  for img in imgs:
    img = np.array(img, dtype=np.float32) * 255.0
    img = np.expand_dims(img, axis=0).astype(np.int8)
    interpreter.set_tensor(input_index, img)
    interpreter.invoke()
    predictions = interpreter.get_tensor(output_index)
    if np.argmax(predictions) == np.argmax(label):
      num_correct += 1

print(f"{num_correct} correct out of {total_seen} images")
quantized_score = float(num_correct) / float(total_seen)
print('Quantized accuracy:', quantized_score)
print('Float accuracy:', score[1])

# Ensure accuracy for quantized TF and TFLite models are similar to original
# model. There is no clear way to measure quantization, but for MNIST
# results which differ a lot likely suggest an error in quantization.
np.testing.assert_allclose(score[1], quantized_score, rtol=0.2, atol=0.2)

Input shape: [-1 51 51  3], Output shape: [-1  6]
Evaluate TFLite model.
0 correct out of 16 images
Quantized accuracy: 0.0
Float accuracy: 0.25


AssertionError: 
Not equal to tolerance rtol=0.2, atol=0.2

Mismatched elements: 1 / 1 (100%)
Max absolute difference: 0.25
Max relative difference: inf
 x: array(0.25)
 y: array(0.)

# Visualize Model Ops

In [8]:
import model_explorer

model_explorer.visualize(quant_file)

ℹ️ Please re-run the cell in each new session

Loading extensions...
Loaded 8 extensions:
 - TFLite adapter (Flatbuffer)
 - TFLite adapter (MLIR)
 - TF adapter (MLIR)
 - TF adapter (direct)
 - GraphDef adapter
 - Pytorch adapter (exported program)
 - MLIR adapter
 - JSON adapter


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Export Model as Header File for Tflite-Micro

In [9]:
!xxd -i {quant_file} > model.h
!cat model.h | sed 's/unsigned char [a-zA-Z_]\+/#define IMG_DIM {IMG_DIM}\nalignas(16) const unsigned char model/g'| sed 's/unsigned int [a-zA-Z_]\+/const unsigned int model_len/g'> temp.h
!mv temp.h model.h
!cat model.h | head -n 2
!cat model.h | tail -n 1

#define IMG_DIM 51
alignas(16) const unsigned char model[] = {
const unsigned int model_len = 68840;


# Export `image_data.h` for testing inference on MCU

In [11]:
# Number of classes in the dataset
NUM_CLASSES = len(class_indices)

# Initialize a dictionary to store one sample per class
sample_per_class = {i: None for i in range(NUM_CLASSES)}
found_classes = set()

# Loop through the validation dataset batches until we collect one sample per class
for x_batch, y_batch in val_dataset_tf:
    # Convert the batch to numpy arrays
    images = x_batch.numpy()
    labels = y_batch.numpy()

    # Loop through each sample in the batch
    for i, label in enumerate(labels):
        class_idx = np.argmax(label)  # Find the class index of the one-hot label

        # If we haven't collected a sample for this class, add it
        if class_idx not in found_classes:
            sample_per_class[class_idx] = images[i]
            found_classes.add(class_idx)

        # Stop if we've found a sample for each class
        if len(found_classes) == NUM_CLASSES:
            break

    if len(found_classes) == NUM_CLASSES:
        break

id_to_class_name = {v: k for k, v in class_indices.items()}

# Define the path for the header file
header_file_path = 'image_data.h'

# Open the file in write mode
with open(header_file_path, 'w') as f:
    # Write a comment at the top of the header file
    f.write("// This header file contains int8 image data arrays for each class\n\n")

    # Loop through each sample in the sample_per_class dictionary
    for class_id, image in sample_per_class.items():
        # Get the class name from the class ID
        class_name = id_to_class_name[class_id]


        image_array = np.array(image, dtype=np.float32)  * 255.0
        image_array = image_array.astype(np.int8)

        # Flatten the image array to 1D for easier embedding into C arrays
        flattened_image_array = image_array.flatten()

        # Write the array definition to the header file
        f.write(f"// Class {class_id}: {class_name}\n")
        f.write(f"{'int8_t' if image_array.dtype==np.int8 else 'float'} {class_name}[] = {{\n")

        # Write the pixel values to the file
        pixel_values = ", ".join(map(str, flattened_image_array))
        f.write(f"    {pixel_values}\n")
        f.write("};\n\n")


print(f"Header file '{header_file_path}' has been created successfully.")

Header file 'image_data.h' has been created successfully.


# Full Quantization [Deprecated, Don't Run This]

---



In [ ]:
# import numpy as np
# def representative_dataset():
#   for data in val_dataset_tf.take(1).take(1):
#     yield [data[0].numpy()]

# converter = tf.lite.TFLiteConverter.from_keras_model(tf_model)
# converter.optimizations = [tf.lite.Optimize.DEFAULT]
# converter.representative_dataset = representative_dataset
# converter._experimental_disable_per_channel_quantization_for_dense_layers = True
# converter.target_spec.supported_ops = [tf.lite.OpsSet.TFLITE_BUILTINS_INT8]
# converter.inference_input_type = tf.uint8  # or tf.uint8
# converter.inference_output_type = tf.uint8  # or tf.uint8
# tflite_noquant_model = converter.convert()



# interpreter = tf.lite.Interpreter(model_content=tflite_noquant_model)
# interpreter.allocate_tensors()
# input_details = interpreter.get_input_details()
# output_details = interpreter.get_output_details()
# input_type = input_details[0]['dtype']
# output_type = output_details[0]['dtype']

# print("Input type:", input_type)
# print("Output type:", output_type)

# !rm model.tflite
# !rm model.h
# with open("model.tflite", 'wb') as f:
#   f.write(tflite_noquant_model)

# !xxd -i model.tflite > model.h
# !cat model.h | sed 's/unsigned char [a-zA-Z_]\+/#define IMG_DIM {IMG_DIM}\nalignas(16) const unsigned char model/g'| sed 's/unsigned int [a-zA-Z_]\+/const unsigned int model_len/g'> temp.h
# !mv temp.h model.h
# !cat model.h | head -n 1
# !cat model.h | tail -n 1


Saved artifact at '/tmp/tmpxx9g_g3_'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 100, 100, 3), dtype=tf.float32, name='keras_tensor')
Output Type:
  TensorSpec(shape=(None, 6), dtype=tf.float32, name=None)
Captures:
  132531359173440: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531359180656: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531359180128: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531359179072: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531359179600: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531360906432: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531359069664: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531359071600: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531359183120: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132531359071952: TensorSpec(shape=(), dtype=tf.resource, name=None)
  13253135906772

/usr/local/lib/python3.10/dist-packages/tensorflow/lite/python/convert.py:983: UserWarning: Statistics for quantized inputs were expected, but not specified; continuing anyway.
  warnings.warn(


Input type: <class 'numpy.uint8'>
Output type: <class 'numpy.uint8'>
rm: cannot remove 'model.h': No such file or directory


# Transferring Weights [Deprecated, Don't Run This]


In [ ]:
# import torch
# import numpy as np
# import tensorflow as tf

# # 1. Collect weights from the PyTorch model
# torch_weights = []

# print("\nTorch Model Parameter Shapes (Sequential):")
# for idx, (name, module) in enumerate(torch_model.named_modules()):
#   # For BatchNorm2d, also collect running mean and variance
#   if isinstance(module, torch.nn.BatchNorm2d):
#       running_mean = module.running_mean.detach().cpu().numpy()
#       running_var = module.running_var.detach().cpu().numpy()
#       gamma = module.weight.detach().cpu().numpy()  # scale
#       beta = module.bias.detach().cpu().numpy()     # shift
#       torch_weights.append(gamma)
#       torch_weights.append(beta)
#       torch_weights.append(running_mean)
#       torch_weights.append(running_var)
#       print(f"Layer {idx}: {name}, Running Mean Shape: {running_mean.shape}, Running Var Shape: {running_var.shape}")
#       continue

#   # Check if the module has `weight` and `bias` attributes
#   if hasattr(module, 'weight') and module.weight is not None:
#       weight = module.weight.detach().cpu().numpy()
#       torch_weights.append(weight)
#       print(f"Layer {idx}: {name}, Weight Shape: {weight.shape}")

#   if hasattr(module, 'bias') and module.bias is not None:
#       bias = module.bias.detach().cpu().numpy()
#       torch_weights.append(bias)
#       print(f"Layer {idx}: {name}, Bias Shape: {bias.shape}")



# # 2. Map PyTorch weights to TensorFlow layers by sequence
# print("\nTensorFlow Model Parameter Shapes (Sequential):")
# torch_weight_idx = 0


# for idx, layer in enumerate(tf_model.layers):
#   # Handle regular layers with weight and bias (e.g., Conv2D, Dense)
#   if layer.weights:  # if the layer has weights
#     temp = torch_weights[0 : len(layer.weights)]
#     torch_weights = torch_weights[len(layer.weights):]
#     print(f"Layer {idx}: {layer.name}")
#     for j in range(len(layer.weights)):
#       print(f"\tWeight: {layer.weights[j].name} \n\t Shape conversion: PyTorch {temp[j].shape} -> Tensorflow {layer.weights[j].shape} ")
#       layer.weights[j].assign(tf.reshape(temp[j], shape=layer.weights[j].shape))



# print("\nWeights transferred successfully from PyTorch to TensorFlow!")



Torch Model Parameter Shapes (Sequential):
Layer 1: conv1, Weight Shape: (16, 3, 3, 3)
Layer 2: bn1, Running Mean Shape: (16,), Running Var Shape: (16,)
Layer 5: dpds.0.0, Weight Shape: (16, 1, 3, 3)
Layer 6: dpds.0.1, Weight Shape: (32, 16, 1, 1)
Layer 7: dpds.0.2, Running Mean Shape: (32,), Running Var Shape: (32,)
Layer 10: dpds.1.0, Weight Shape: (32, 1, 3, 3)
Layer 11: dpds.1.1, Weight Shape: (40, 32, 1, 1)
Layer 12: dpds.1.2, Running Mean Shape: (40,), Running Var Shape: (40,)
Layer 16: dpds.1.4.fc1, Weight Shape: (6, 40, 1, 1)
Layer 16: dpds.1.4.fc1, Bias Shape: (6,)
Layer 17: dpds.1.4.fc2, Weight Shape: (40, 6, 1, 1)
Layer 17: dpds.1.4.fc2, Bias Shape: (40,)
Layer 19: dpds.2.0, Weight Shape: (40, 1, 3, 3)
Layer 20: dpds.2.1, Weight Shape: (48, 40, 1, 1)
Layer 21: dpds.2.2, Running Mean Shape: (48,), Running Var Shape: (48,)
Layer 24: dpds.3.0, Weight Shape: (48, 1, 3, 3)
Layer 25: dpds.3.1, Weight Shape: (96, 48, 1, 1)
Layer 26: dpds.3.2, Running Mean Shape: (96,), Running Var

# Splitting Dataset Into Train, Test, and, Split Subdirectories [Deprecated, Don't Run This]


In [ ]:
# import logging
# logging.getLogger("tensorflow").setLevel(logging.DEBUG)

# import tensorflow as tf
# from tensorflow import keras
# import numpy as np
# import pathlib
# import os
# import shutil
# import numpy as np
# from sklearn.model_selection import train_test_split

# # Path to the dataset
# dataset_dir = '/content/Merged'
# output_dir = '/content/Merged_Split'  # Where to save the split dataset

# # List of all class labels (subfolder names)
# class_labels = os.listdir(dataset_dir)
# class_labels = [label for label in class_labels if os.path.isdir(os.path.join(dataset_dir, label))]  # Filter out any non-directories

# # Create directories for train, val, and test splits
# split_dirs = ['train', 'val', 'test']
# for split in split_dirs:
#     split_path = os.path.join(output_dir, split)
#     if not os.path.exists(split_path):
#         os.makedirs(split_path)
#     for label in class_labels:
#         os.makedirs(os.path.join(split_path, label))

# # Iterate over each class and split the dataset
# for label in class_labels:
#     label_dir = os.path.join(dataset_dir, label)
#     images = os.listdir(label_dir)
#     images = [os.path.join(label_dir, img) for img in images if os.path.isfile(os.path.join(label_dir, img))]

#     # Split the images into train, val, and test sets
#     train_images, test_images = train_test_split(images, test_size=0.2, random_state=42)
#     val_images, test_images = train_test_split(test_images, test_size=0.5, random_state=42)

#     # Move the images to their respective folders
#     for split, image_list in zip(['train', 'val', 'test'], [train_images, val_images, test_images]):
#         for image in image_list:
#             shutil.copy(image, os.path.join(output_dir, split, label, os.path.basename(image)))

# # Check the directory structure
# print("Dataset split completed!")
# !zip -r Merged_Split.zip Merged_Split
# from google.colab import drive
# drive.mount('/content/drive')
# !cp -rf Merged_Split.zip /content/drive/MyDrive/TrashDatasetMerged/


Dataset split completed!
